In [1]:
import numpy as np

%matplotlib inline
import matplotlib.pyplot as plt

%load_ext autoreload
%autoreload 2

import sys
sys.path.append('../')
import scripts.load_dataset as load_dataset
import scripts.map_and_average as mapper
import scripts.classification
import scripts.outliers as outliers

/homes/mp305/anaconda/lib/python2.7/site-packages/librosa/core/audio.py:33: UserWarning: Could not import scikits.samplerate. Falling back to scipy.signal
  warnings.warn('Could not import scikits.samplerate. '


In [ ]:
OUTPUT_FILES = load_dataset.OUTPUT_FILES
n_iters = 10
df = load_dataset.sample_dataset(csv_file=load_dataset.METADATA_FILE)

/homes/mp305/anaconda/lib/python2.7/site-packages/IPython/core/interactiveshell.py:2822: DtypeWarning: Columns (0,1,2,4,5,6,7,8,10,11,12,13,14,15,16,17,19,21,22,23,24,25,26,27,29,31,35,38,39,40,41,44,45,48,55,56,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72,73,74,75,76,77,78,79,80,81,82,83,84,85,86,93,95,96) have mixed types. Specify dtype option on import or set low_memory=False.
  if self.run_code(code, result):


In [ ]:
df.shape

In [ ]:
for n in range(n_iters):
    print "iteration %d" % n
    load_dataset.OUTPUT_FILES = [output_file.split('.pickle')[0]+'_'+str(n)+'.pickle' for 
                                 output_file in OUTPUT_FILES]
    load_dataset.features_for_train_test_sets(df, write_output=True)

iteration 0
file 0 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 1 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 2 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 3 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 4 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 5 of 5037
loading speech/music segments...
extracting onset patterns and 

file 47 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
file 48 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
file 49 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
file 50 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
file 51 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
file 52 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
file 53 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
file 54 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
file 55 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 56 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load

extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 97 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 98 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 99 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 100 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-melody-8sec/
file 101 of 5037
loading speech/music segments...
extracting onset patterns and mfccs...
extracting chroma...
load precomputed pitch bihist /import/c4dm-05/mariap/Melodia-m

In [ ]:
for n in range(n_iters):
    print "iteration %d" % n
    
    print "mapping..."
    mapper.INPUT_FILES = [output_file.split('.pickle')[0]+'_'+str(n)+'.pickle' for 
                                 output_file in OUTPUT_FILES]
    _, _, ldadata_list, _, _, Y, Yaudio = mapper.lda_map_and_average_frames(min_variance=0.99)
    X = np.concatenate(ldadata_list)
    
    # classification and confusion
    print "classifying..."
    traininds, testinds = classification.get_train_test_indices()
    X_train, Y_train, X_test, Y_test = classification.get_train_test_sets(X, Y, traininds, testinds)
    accuracy, _ = classification.confusion_matrix(X_train, Y_train, X_test, Y_test, saveCF=False, plots=False)
    print accuracy
    
    # outliers
    print "detecting outliers..."
    ddf = outliers.load_metadata(Yaudio, metadata_file=load_dataset.METADATA_FILE)
    df_global, threshold, MD = get_outliers_df(X, Y, chi2thr=0.999)
    print_most_least_outliers_topN(df_global, N=10)
    
    # write output
    print "writing file"
    df_global.to_csv('../data/outliers_'+str(n)+'.csv', index=False)